In [6]:
pip install -q holoviews==1.18.0

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.3/4.3 MB 32.8 MB/s eta 0:00:00


In [30]:
pip install -q netcdf4

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.0/9.0 MB 35.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 51.2 MB/s eta 0:00:00


In [50]:
pip install -q hvplot

In [51]:
pip install -q jupyter_bokeh

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 148.6/148.6 kB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.4/139.4 kB 6.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 27.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 36.7 MB/s eta 0:00:00


# From Echosounders to Echograms

At a given time, an echosounder emits a signal and records the backscatter. For a given ping time, the backscatter is recorded at a regular sequence of times. Each measured value is called a sample, and if we have $N$ samples, indexed $0,..., N-1$ and the zero'th one is closest to the transducer. The time for each measurement can be transformed into a range variable corresponding to the distance from the transducer. The range can be calculated as $R_i = t_i \times c /2$, where $t_i$ is the time elapsed from the `ping_time` to the $i^{th}$ measurement, $c$ is the speed of sound calculated based on the calibration information, and the division by two accounts for the signal travel to and from the reflected object. If the range does not change over time, one can obtain for each frequency a 2D array of backscatter values, that can be plotted as an image: an *echogram*.

Visualization of range samples from Echoview: https://support.echoview.com/WebHelp/Reference/About_start_and_stop_ranges.htm

### Moored Upward-Looking Echosounder

First we will discuss the case of a moored upward-looking echounder. It records the backscatter profile of the water column at a fixed location over a period of time.

We will read a data set from the [Ocean Observatories Initiative](https://oceanobservatories.org/) which has multiple echosounder deployments some collecting data over cabled arrays since 2015 (with interruptions due to instrument failures). The data is public and we will use a small sonar file example which is already stored in an easy to read `netcdf` format.

In [52]:
import xarray as xr

In [53]:
# Reading a subset from a bigger dataset

In [54]:
# ds = xr.open_dataset("OOI_30_Days_Test_Input.nc")

In [55]:
# we will select a small subset of a few days
# ds.Sv.isel(channel=2)[1250:-150].T.plot()

In [56]:
# ds.Sv[:,1250:-150,:].to_netcdf("OOI_Sv.nc")

In [57]:
ds = xr.open_dataset("OOI_Sv.nc")

In [58]:
ds

<xarray.Dataset>
Dimensions:     (echo_range: 205, ping_time: 242, channel: 3)
Coordinates:
  * echo_range  (echo_range) float64 0.0 1.0 2.0 3.0 ... 201.0 202.0 203.0 204.0
  * ping_time   (ping_time) datetime64[ns] 2017-08-25T14:30:00 ... 2017-08-29...
  * channel     (channel) object 'GPT  38 kHz 00907208dd13 5-1 OOI.38|200' .....
Data variables:
    Sv          (channel, ping_time, echo_range) float64 ...

The `Sv` array contains the volume backscattering strength. We can see that the dimensions are `(echo_range, ping_time, channel)`. This data set has 3 frequencies each stored as a channel.

In [59]:
ds.channel

<xarray.DataArray 'channel' (channel: 3)>
array(['GPT  38 kHz 00907208dd13 5-1 OOI.38|200',
       'GPT 120 kHz 00907208a0b1 3-1 ES120-7CD',
       'GPT 200 kHz 00907208dd13 5-2 OOI38|200'], dtype=object)
Coordinates:
  * channel  (channel) object 'GPT  38 kHz 00907208dd13 5-1 OOI.38|200' ... '...
Attributes:
    long_name:  Vendor channel ID

In [60]:
import hvplot.xarray

In [61]:
import panel as pn

In [63]:
hvplot.extension('bokeh')
from panel.io.notebook import load_notebook
load_notebook()
pn.panel(ds.hvplot.quadmesh(x="ping_time", y="echo_range").opts(cmap="jet"))

Row
    [0] HoloViews(DynamicMap, height=300, sizing_mode='fixed', width=700)
    [1] WidgetBox(align=('end', 'start'))
        [0] Select(margin=(20, 20, 20, 20), name='Vendor channel ID', options=['GPT  38 kHz 00907208dd13...], value='GPT  38 kHz 0..., width=250)